In [16]:
import torch
from torch_geometric.data import Data

import uproot
import torch
from torch_geometric.data import Data
import numpy as np
import torch
from torch_geometric.nn import GCNConv
import torch.nn.functional as F
import torch.nn as nn


# Open the ROOT file and tree using uproot
file = uproot.open("/eos/user/h/hsharma/PythiaFIles/Cascades_Xi/cascade_data.root")
tree = file["cascade_tree"]

# Load only the first 5000 entries
branches = ["px", "py", "pz", "pT", "eta", "phi", "charge", "pid", "isXi"]
data = tree.arrays(branches, library="np", entry_stop=5000)  # Limits the number of entries

px, py, pz = data["px"], data["py"], data["pz"]
pT, eta, phi = data["pT"], data["eta"], data["phi"]
charge, pid, isXi = data["charge"], data["pid"], data["isXi"]

# Initialize list to store graph data
graphs = []


# Loop through events (now only for 5000 entries)
for event_idx in range(len(px)):
    if isinstance(px[event_idx], np.ndarray):  # If px is an array of tracks
        nodes = []
        num_tracks = len(px[event_idx])  # Number of tracks in the event

        for i in range(num_tracks):  # Iterate over tracks in the event
            nodes.append([px[event_idx][i], py[event_idx][i], pz[event_idx][i], 
                          pT[event_idx][i], eta[event_idx][i], phi[event_idx][i], 
                          charge[event_idx][i], pid[event_idx][i]])

        # Convert to tensor (PyTorch)
        node_features = torch.tensor(nodes, dtype=torch.float)

        # Construct edges (example: connect tracks from the same event)
        edge_index = []
        for i in range(num_tracks):
            for j in range(i + 1, num_tracks):
                if some_condition:  # Define a condition, e.g., invariant mass, DCA
                    edge_index.append([i, j])
                    edge_index.append([j, i])

        edge_index = torch.tensor(edge_index, dtype=torch.long).t().contiguous()

    else:  # For single track events, directly process it
        # Single track, no need to loop over tracks
        nodes = [[px[event_idx], py[event_idx], pz[event_idx], pT[event_idx], 
                  eta[event_idx], phi[event_idx], charge[event_idx], pid[event_idx]]]
        
        # Convert to tensor (PyTorch)
        node_features = torch.tensor(nodes, dtype=torch.float)

        # No edges for single track events, add self-loops (optional)
        edge_index = torch.tensor([[0], [0]], dtype=torch.long)  # Self-loop for the single track

    # Example target (1 for Xi, 0 for non-cascade decay)
    target = 1 if isXi[event_idx] == 1 else 0
    
    # Create a graph data object
    graph_data = Data(x=node_features, edge_index=edge_index, y=torch.tensor([target], dtype=torch.float))
    graphs.append(graph_data)


###----------------- MODEL Defination 


class GNNModel(torch.nn.Module):
    def __init__(self, input_dim, hidden_dim, output_dim):
        super(GNNModel, self).__init__()
        self.conv1 = GCNConv(input_dim, hidden_dim)
        self.conv2 = GCNConv(hidden_dim, output_dim)
        self.fc = nn.Linear(input_dim, output_dim)

        # Initialize GCNConv weights using Xavier
        torch.nn.init.xavier_uniform_(self.conv1.lin.weight)  # Accessing the internal linear layer of GCNConv
        torch.nn.init.xavier_uniform_(self.conv2.lin.weight)  # Same for conv2
        
        # Initialize biases if they exist
        if self.conv1.lin.bias is not None:
            torch.nn.init.zeros_(self.conv1.lin.bias)  # Initialize bias to zero
        if self.conv2.lin.bias is not None:
            torch.nn.init.zeros_(self.conv2.lin.bias)

        # Initialize fully connected layer
        torch.nn.init.xavier_uniform_(self.fc.weight)
        torch.nn.init.zeros_(self.fc.bias)

    def forward(self, data):
        x, edge_index = data.x, data.edge_index

        if torch.isnan(x).any():
            print(f"NaN detected in input features: {x}")

        # Apply the first GCN layer
        x = self.conv1(x, edge_index)
        if torch.isnan(x).any():
            print(f"NaN detected after conv1: {x}")

        x = F.relu(x)

        # Apply the second GCN layer
        x = self.conv2(x, edge_index)
        if torch.isnan(x).any():
            print(f"NaN detected after conv2: {x}")

        return F.log_softmax(x, dim=1)


class GCNModel(nn.Module):
    def __init__(self):
        super(GCNModel, self).__init__()
        self.conv1 = GCNConv(in_channels=16, out_channels=32)  # Example channels
        self.conv2 = GCNConv(in_channels=32, out_channels=2)   # Final output layer

    def forward(self, data):
        x, edge_index = data.x, data.edge_index

        # Apply first graph convolution layer and relu activation
        x = self.conv1(x, edge_index)
        x = F.relu(x)
        
        # Apply second graph convolution layer
        x = self.conv2(x, edge_index)
        
        return x
    


class SimpleGCNModel(nn.Module):
    def __init__(self):
        super(SimpleGCNModel, self).__init__()
        # Example with GCN layers or regular layers that have learnable parameters
        self.conv1 = nn.Linear(16, 32)  # A linear layer (replace with your graph conv layer)
        self.conv2 = nn.Linear(32, 2)   # Final output layer

    def forward(self, data):
        # Forward pass
        x = data.x  # Node features
        edge_index = data.edge_index  # Graph structure
        
        # Apply layers
        x = F.relu(self.conv1(x))  # Apply relu after first layer
        x = self.conv2(x)  # Second layer (output layer)
        
        return x
    
    
    
# Define the model
model = GNNModel(input_dim=8, hidden_dim=64, output_dim=2)  # Example input/output dims

# Set up optimizer and loss function
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)

criterion = torch.nn.CrossEntropyLoss()


    
# Training loop
num_epochs = 2
# Training loop
# Training loop
for epoch in range(num_epochs):
    model.train()  # Ensure model is in training mode

    total_loss = 0  # Track total loss for this epoch

    # Loop through all graphs in the dataset
    for graph_data in graphs:
        x, edge_index = graph_data.x, graph_data.edge_index
        target = graph_data.y.long()  # Ensure target labels are Long (required by CrossEntropyLoss)

        # Handle empty edge_index (no edges case) for multi-node graphs
        if edge_index.numel() == 0:  # No edges in the graph
            num_nodes = x.size(0)
            # Create a self-loop for each node, i.e., connect each node to itself
            edge_index = torch.arange(0, num_nodes, dtype=torch.long).view(1, -1).repeat(2, 1)
            #print("edge_index corrected to:", edge_index)

        # Check edge_index shape for debugging
        #print("edge_index shape:", edge_index.shape)

        # Forward pass
        output = model(graph_data)  # Get predictions

        # Compute loss
        loss = criterion(output, target)  # Assuming `graph_data.y` contains labels

        optimizer.zero_grad()  # Zero gradients before backward pass

        # Backward pass and optimization
        loss.backward()  # Compute gradients
        # Clip gradients to avoid explosion
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)

        optimizer.step()  # Update model parameters
        total_loss += loss.item()  # Accumulate loss for this graph

    # Print average loss for this epoch
    print(f'Epoch {epoch+1}/{num_epochs}, Average Loss: {total_loss / len(graphs)}')


NaN detected in input features: tensor([[  0.0000,   0.0000, -12.4335,   0.0000,      nan,   0.0000,   0.0000,
          21.0000]])
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]],

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]],

...

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected in input features: tensor([[ 0.0000e+00,  0.0000e+00, -1.5496e-03,  0.0000e+00,         nan,
          0.0000e+00,  0.0000e+00,  2.1000e+01]])
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan,
         nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]],
       grad_fn=<AddBackward0>)
NaN detected after conv2: tensor([[nan, nan]], grad_fn=<AddBackward0>)
NaN detected after conv1: tensor([[nan, nan, n

In [15]:


# Forward pass
output = model(graph_data)  # Get predictions

print(f"Model output: {output}")
print(f"Target: {target}")

if edge_index.size(1) == 0:  # No edges, skip this graph
    print(f"Skipping graph {event_idx} with no edges")
    continue


Model output: tensor([[nan, nan]], grad_fn=<LogSoftmaxBackward0>)
Target: tensor([0])


SyntaxError: 'continue' not properly in loop (2363834669.py, line 9)